In [0]:
client_id=""
tenant_id=""
client_secret=""

spark.conf.set("fs.azure.account.auth.type.storagedatafactory2605.dfs.core.windows.net", "OAuth")
spark.conf.set("fs.azure.account.oauth.provider.type.storagedatafactory2605.dfs.core.windows.net",
               "org.apache.hadoop.fs.azurebfs.oauth2.ClientCredsTokenProvider")

spark.conf.set("fs.azure.account.oauth2.client.id.storagedatafactory2605.dfs.core.windows.net", client_id)
spark.conf.set("fs.azure.account.oauth2.client.secret.storagedatafactory2605.dfs.core.windows.net", client_secret)

spark.conf.set("fs.azure.account.oauth2.client.endpoint.storagedatafactory2605.dfs.core.windows.net",
               f"https://login.microsoftonline.com/{tenant_id}/oauth2/token")


In [0]:
display(dbutils.fs.ls("abfss://fsilver@storagedatafactory2605.dfs.core.windows.net/"))


path name size modificationTime abfss://fsilver@storagedatafactory2605.dfs.core.windows.net/api_docs_delta/ api_docs_delta/ 0 1763209641000 abfss://fsilver@storagedatafactory2605.dfs.core.windows.net/cleaned_logs_delta/ cleaned_logs_delta/ 0 1763208857000 abfss://fsilver@storagedatafactory2605.dfs.core.windows.net/supply_chain_delta/ supply_chain_delta/ 0 1763209201000

In [0]:
df_supply = spark.read.format("delta").load(
    "abfss://fsilver@storagedatafactory2605.dfs.core.windows.net/supply_chain_delta/"
)
df_supply.printSchema()


root
 |-- order_id: integer (nullable = true)
 |-- order_item_id: integer (nullable = true)
 |-- order_customer_id: integer (nullable = true)
 |-- product_name: string (nullable = true)
 |-- product_price: double (nullable = true)
 |-- product_category_id: integer (nullable = true)
 |-- category_name: string (nullable = true)
 |-- product_description: string (nullable = true)
 |-- order_ts: timestamp (nullable = true)
 |-- ship_ts: timestamp (nullable = true)
 |-- order_year: integer (nullable = true)
 |-- order_month: integer (nullable = true)
 |-- order_ym: string (nullable = true)
 |-- order_item_quantity: integer (nullable = true)
 |-- sales: double (nullable = true)
 |-- order_item_total: double (nullable = true)
 |-- order_profit_per_order: double (nullable = true)
 |-- benefit_per_order: double (nullable = true)
 |-- market: string (nullable = true)
 |-- order_region: string (nullable = true)
 |-- order_state: string (nullable = true)



In [0]:
import pyspark.sql.functions as F

df_monthly = (
    df_supply
    .groupBy("product_name", "category_name", "order_year", "order_month", "order_ym")
    .agg(
        F.sum("sales").alias("monthly_sales"),
        F.sum("order_item_quantity").alias("monthly_quantity")
    )
    .orderBy("product_name", "order_year", "order_month")
)


In [0]:
from pyspark.sql.window import Window

w = Window.partitionBy("product_name").orderBy("order_year", "order_month")

df_monthly = (
    df_monthly
    .withColumn("lag_1_sales", F.lag("monthly_sales", 1).over(w))
    .withColumn("lag_3_sales", F.lag("monthly_sales", 3).over(w))
    .withColumn("rmean_3_sales", F.avg("monthly_sales").over(w.rowsBetween(-2, 0)))
)


In [0]:
df_monthly = df_monthly.withColumn(
    "target_next_month_sales",
    F.lead("monthly_sales", 1).over(w)
)


In [0]:
display(df_monthly.limit(20))


product_name category_name order_year order_month order_ym monthly_sales monthly_quantity lag_1_sales lag_3_sales rmean_3_sales target_next_month_sales adidas brazuca 2014 official match ball baseball & softball 2017 4 2017-04 799.9500275 5 null null 799.9500275 2399.8500825 adidas brazuca 2014 official match ball baseball & softball 2017 5 2017-05 2399.8500825 15 799.9500275 null 1599.900055 1919.880066 adidas brazuca 2014 official match ball baseball & softball 2017 6 2017-06 1919.880066 12 2399.8500825 null 1706.5600586666667 2239.8600770000003 adidas brazuca 2014 official match ball baseball & softball 2017 7 2017-07 2239.8600770000003 14 1919.880066 799.9500275 2186.530075166667 2239.8600770000003 adidas brazuca 2014 official match ball baseball & softball 2017 8 2017-08 2239.8600770000003 14 2239.8600770000003 2399.8500825 2133.2000733333334 799.9500275 adidas brazuca 2014 official match ball baseball & softball 2017 9 2017-09 799.9500275 5 2239.8600770000003 1919.880066 1759.8900605000001 null adidas kids' f5 messi fg soccer cleat baseball & softball 2015 1 2015-01 629.82001486 18 null null 629.82001486 699.80002208 adidas kids' f5 messi fg soccer cleat baseball & softball 2015 2 2015-02 699.80002208 20 629.82001486 null 664.8100184699999 454.87001414 adidas kids' f5 messi fg soccer cleat baseball & softball 2015 3 2015-03 454.87001414 13 699.80002208 null 594.8300170266666 1119.68001538 adidas kids' f5 messi fg soccer cleat baseball & softball 2015 4 2015-04 1119.68001538 32 454.87001414 629.82001486 758.1166838666667 874.75002664 adidas kids' f5 messi fg soccer cleat baseball & softball 2015 5 2015-05 874.75002664 25 1119.68001538 699.80002208 816.4333520533334 559.84001152 adidas kids' f5 messi fg soccer cleat baseball & softball 2015 6 2015-06 559.84001152 16 874.75002664 454.87001414 851.4233511799999 1049.70002736 adidas kids' f5 messi fg soccer cleat baseball & softball 2015 7 2015-07 1049.70002736 30 559.84001152 1119.68001538 828.0966885066667 699.80002586 adidas kids' f5 messi fg soccer cleat baseball & softball 2015 8 2015-08 699.80002586 20 1049.70002736 874.75002664 769.7800215799999 1224.65001656 adidas kids' f5 messi fg soccer cleat baseball & softball 2015 9 2015-09 1224.65001656 35 699.80002586 559.84001152 991.3833565933334 279.92001344 adidas kids' f5 messi fg soccer cleat baseball & softball 2015 10 2015-10 279.92001344 8 1224.65001656 1049.70002736 734.79001862 1679.52002688 adidas kids' f5 messi fg soccer cleat baseball & softball 2015 11 2015-11 1679.52002688 48 279.92001344 699.80002586 1061.3633522933333 1364.61001562 adidas kids' f5 messi fg soccer cleat baseball & softball 2015 12 2015-12 1364.61001562 39 1679.52002688 1224.65001656 1108.0166853133333 874.75003426 adidas kids' f5 messi fg soccer cleat baseball & softball 2016 1 2016-01 874.75003426 25 1364.61001562 279.92001344 1306.29335892 1119.6800230200001 adidas kids' f5 messi fg soccer cleat baseball & softball 2016 2 2016-02 1119.6800230200001 32 874.75003426 1679.52002688 1119.6800243 839.76000198

In [0]:
gold_monthly_path = "abfss://fgold@storagedatafactory2605.dfs.core.windows.net/monthly_sales_delta/"

df_monthly.write.format("delta").mode("overwrite").save(gold_monthly_path)


In [0]:
display(dbutils.fs.ls(gold_monthly_path))


path name size modificationTime abfss://fgold@storagedatafactory2605.dfs.core.windows.net/monthly_sales_delta/_delta_log/ _delta_log/ 0 1763223098000 abfss://fgold@storagedatafactory2605.dfs.core.windows.net/monthly_sales_delta/part-00000-3f21887b-6444-480e-bf2b-1ec502eacc48.c000.snappy.parquet part-00000-3f21887b-6444-480e-bf2b-1ec502eacc48.c000.snappy.parquet 72933 1763223099000 abfss://fgold@storagedatafactory2605.dfs.core.windows.net/monthly_sales_delta/part-00000-ba025aca-6326-481f-b1d8-5d361af85bf7.c000.snappy.parquet part-00000-ba025aca-6326-481f-b1d8-5d361af85bf7.c000.snappy.parquet 72933 1763224086000

In [0]:
gold_monthly_path = "abfss://fgold@storagedatafactory2605.dfs.core.windows.net/monthly_sales_delta/"

df_monthly = spark.read.format("delta").load(gold_monthly_path)

display(df_monthly)
df_monthly.printSchema()


product_name category_name order_year order_month order_ym monthly_sales monthly_quantity lag_1_sales lag_3_sales rmean_3_sales target_next_month_sales adidas brazuca 2014 official match ball baseball & softball 2017 4 2017-04 799.9500275 5 null null 799.9500275 2399.8500825 adidas brazuca 2014 official match ball baseball & softball 2017 5 2017-05 2399.8500825 15 799.9500275 null 1599.900055 1919.880066 adidas brazuca 2014 official match ball baseball & softball 2017 6 2017-06 1919.880066 12 2399.8500825 null 1706.5600586666667 2239.8600770000003 adidas brazuca 2014 official match ball baseball & softball 2017 7 2017-07 2239.8600770000003 14 1919.880066 799.9500275 2186.530075166667 2239.8600770000003 adidas brazuca 2014 official match ball baseball & softball 2017 8 2017-08 2239.8600770000003 14 2239.8600770000003 2399.8500825 2133.2000733333334 799.9500275 adidas brazuca 2014 official match ball baseball & softball 2017 9 2017-09 799.9500275 5 2239.8600770000003 1919.880066 1759.8900605000001 null adidas kids' f5 messi fg soccer cleat baseball & softball 2015 1 2015-01 629.82001486 18 null null 629.82001486 699.80002208 adidas kids' f5 messi fg soccer cleat baseball & softball 2015 2 2015-02 699.80002208 20 629.82001486 null 664.8100184699999 454.87001414 adidas kids' f5 messi fg soccer cleat baseball & softball 2015 3 2015-03 454.87001414 13 699.80002208 null 594.8300170266666 1119.68001538 adidas kids' f5 messi fg soccer cleat baseball & softball 2015 4 2015-04 1119.68001538 32 454.87001414 629.82001486 758.1166838666667 874.75002664 adidas kids' f5 messi fg soccer cleat baseball & softball 2015 5 2015-05 874.75002664 25 1119.68001538 699.80002208 816.4333520533334 559.84001152 adidas kids' f5 messi fg soccer cleat baseball & softball 2015 6 2015-06 559.84001152 16 874.75002664 454.87001414 851.4233511799999 1049.70002736 adidas kids' f5 messi fg soccer cleat baseball & softball 2015 7 2015-07 1049.70002736 30 559.84001152 1119.68001538 828.0966885066667 699.80002586 adidas kids' f5 messi fg soccer cleat baseball & softball 2015 8 2015-08 699.80002586 20 1049.70002736 874.75002664 769.7800215799999 1224.65001656 adidas kids' f5 messi fg soccer cleat baseball & softball 2015 9 2015-09 1224.65001656 35 699.80002586 559.84001152 991.3833565933334 279.92001344 adidas kids' f5 messi fg soccer cleat baseball & softball 2015 10 2015-10 279.92001344 8 1224.65001656 1049.70002736 734.79001862 1679.52002688 adidas kids' f5 messi fg soccer cleat baseball & softball 2015 11 2015-11 1679.52002688 48 279.92001344 699.80002586 1061.3633522933333 1364.61001562 adidas kids' f5 messi fg soccer cleat baseball & softball 2015 12 2015-12 1364.61001562 39 1679.52002688 1224.65001656 1108.0166853133333 874.75003426 adidas kids' f5 messi fg soccer cleat baseball & softball 2016 1 2016-01 874.75003426 25 1364.61001562 279.92001344 1306.29335892 1119.6800230200001 adidas kids' f5 messi fg soccer cleat baseball & softball 2016 2 2016-02 1119.6800230200001 32 874.75003426 1679.52002688 1119.6800243 839.76000198 adidas kids' f5 messi fg soccer cleat baseball & softball 2016 3 2016-03 839.76000198 24 1119.6800230200001 1364.61001562 944.7300197533335 1329.6200139399998 adidas kids' f5 messi fg soccer cleat baseball & softball 2016 4 2016-04 1329.6200139399998 38 839.76000198 874.75003426 1096.3533463133333 839.7599943199999 adidas kids' f5 messi fg soccer cleat baseball & softball 2016 5 2016-05 839.7599943199999 24 1329.6200139399998 1119.6800230200001 1003.0466700799999 664.81001656 adidas kids' f5 messi fg soccer cleat baseball & softball 2016 6 2016-06 664.81001656 19 839.7599943199999 839.76000198 944.7300082733332 2064.41005298 adidas kids' f5 messi fg soccer cleat baseball & softball 2016 7 2016-07 2064.41005298 59 664.81001656 1329.6200139399998 1189.6600212866667 699.80001056 adidas kids' f5 messi fg soccer cleat baseball & softball 2016 8 2016-08 699.80001056 20 2064.41005298 839.7599943199999 1143.0066933666665 524.85000984 adidas kids' f5 

root
 |-- product_name: string (nullable = true)
 |-- category_name: string (nullable = true)
 |-- order_year: integer (nullable = true)
 |-- order_month: integer (nullable = true)
 |-- order_ym: string (nullable = true)
 |-- monthly_sales: double (nullable = true)
 |-- monthly_quantity: long (nullable = true)
 |-- lag_1_sales: double (nullable = true)
 |-- lag_3_sales: double (nullable = true)
 |-- rmean_3_sales: double (nullable = true)
 |-- target_next_month_sales: double (nullable = true)



In [0]:
display(df_monthly.limit(10))

product_name category_name order_year order_month order_ym monthly_sales monthly_quantity lag_1_sales lag_3_sales rmean_3_sales target_next_month_sales adidas brazuca 2014 official match ball baseball & softball 2017 4 2017-04 799.9500275 5 null null 799.9500275 2399.8500825 adidas brazuca 2014 official match ball baseball & softball 2017 5 2017-05 2399.8500825 15 799.9500275 null 1599.900055 1919.880066 adidas brazuca 2014 official match ball baseball & softball 2017 6 2017-06 1919.880066 12 2399.8500825 null 1706.5600586666667 2239.8600770000003 adidas brazuca 2014 official match ball baseball & softball 2017 7 2017-07 2239.8600770000003 14 1919.880066 799.9500275 2186.530075166667 2239.8600770000003 adidas brazuca 2014 official match ball baseball & softball 2017 8 2017-08 2239.8600770000003 14 2239.8600770000003 2399.8500825 2133.2000733333334 799.9500275 adidas brazuca 2014 official match ball baseball & softball 2017 9 2017-09 799.9500275 5 2239.8600770000003 1919.880066 1759.8900605000001 null adidas kids' f5 messi fg soccer cleat baseball & softball 2015 1 2015-01 629.82001486 18 null null 629.82001486 699.80002208 adidas kids' f5 messi fg soccer cleat baseball & softball 2015 2 2015-02 699.80002208 20 629.82001486 null 664.8100184699999 454.87001414 adidas kids' f5 messi fg soccer cleat baseball & softball 2015 3 2015-03 454.87001414 13 699.80002208 null 594.8300170266666 1119.68001538 adidas kids' f5 messi fg soccer cleat baseball & softball 2015 4 2015-04 1119.68001538 32 454.87001414 629.82001486 758.1166838666667 874.75002664

In [0]:
from pyspark.sql import functions as F

df_monthly = df_monthly.withColumn(
    "mom_growth",
    (F.col("monthly_sales") - F.col("lag_1_sales")) / F.col("lag_1_sales")
)


In [0]:
from pyspark.sql.window import Window

w = Window.partitionBy("product_name").orderBy("order_year", "order_month")

df_monthly = df_monthly.withColumn(
    "lag_12_sales",
    F.lag("monthly_sales", 12).over(w)
)

df_monthly = df_monthly.withColumn(
    "yoy_growth",
    (F.col("monthly_sales") - F.col("lag_12_sales")) / F.col("lag_12_sales")
)


In [0]:
df_monthly = df_monthly.withColumn(
    "rmean_6_sales",
    F.avg("monthly_sales").over(w.rowsBetween(-5, 0))
)


In [0]:
df_monthly.select("product_name", "order_ym", "monthly_sales", "mom_growth", "yoy_growth", "rmean_6_sales").show(10)


+--------------------+--------+------------------+--------------------+----------+------------------+
|        product_name|order_ym|     monthly_sales|          mom_growth|yoy_growth|     rmean_6_sales|
+--------------------+--------+------------------+--------------------+----------+------------------+
|adidas brazuca 20...| 2017-04|       799.9500275|                NULL|      NULL|       799.9500275|
|adidas brazuca 20...| 2017-05|      2399.8500825|                 2.0|      NULL|       1599.900055|
|adidas brazuca 20...| 2017-06|       1919.880066|-0.20000000000000007|      NULL|1706.5600586666667|
|adidas brazuca 20...| 2017-07|2239.8600770000003| 0.16666666666666685|      NULL|     1839.88506325|
|adidas brazuca 20...| 2017-08|2239.8600770000003|                 0.0|      NULL|1919.8800660000002|
|adidas brazuca 20...| 2017-09|       799.9500275| -0.6428571428571429|      NULL|1733.2250595833332|
|adidas kids' f5 m...| 2015-01|      629.82001486|                NULL|      NULL|

In [0]:
df_monthly.write.format("delta").mode("overwrite").save("abfss://fgold@storagedatafactory2605.dfs.core.windows.net/monthly_sales_enriched_delta/")


In [0]:
display(dbutils.fs.ls("abfss://fgold@storagedatafactory2605.dfs.core.windows.net/monthly_sales_enriched_delta/"))


path name size modificationTime abfss://fgold@storagedatafactory2605.dfs.core.windows.net/monthly_sales_enriched_delta/_delta_log/ _delta_log/ 0 1763223574000 abfss://fgold@storagedatafactory2605.dfs.core.windows.net/monthly_sales_enriched_delta/part-00000-b401a2ec-0913-4668-b9db-91762b298c82.c000.snappy.parquet part-00000-b401a2ec-0913-4668-b9db-91762b298c82.c000.snappy.parquet 114408 1763223574000 abfss://fgold@storagedatafactory2605.dfs.core.windows.net/monthly_sales_enriched_delta/part-00000-e8583eb5-b2cb-40e7-b01b-945b86377730.c000.snappy.parquet part-00000-e8583eb5-b2cb-40e7-b01b-945b86377730.c000.snappy.parquet 114408 1763224092000

In [0]:
logs_silver_path = "abfss://fsilver@storagedatafactory2605.dfs.core.windows.net/cleaned_logs_delta/"

df_logs = spark.read.format("delta").load(logs_silver_path)

display(df_logs)
df_logs.printSchema()


product category DATE MONTH HOUR department ip url event_ts perfect fitness perfect rip deck cleats 9/1/2017 18:25 Sep 18 apparel 19.239.13.199 /department/apparel/category/cleats/product/Perfect%20Fitness%20Perfect%20Rip%20Deck 2017-09-01T18:25:00Z yakima doubledown ace hitch mount 4-bike rack strength training 9/1/2017 18:25 Sep 18 footwear 61.230.25.199 /department/footwear/category/strength%20training/product/Yakima%20DoubleDown%20Ace%20Hitch%20Mount%204-Bike%20Rack 2017-09-01T18:25:00Z top flite women's 2017 xl hybrid golf apparel 9/1/2017 18:26 Sep 18 outdoors 16.231.175.0 /department/outdoors/category/golf%20apparel/product/Top%20Flite%20Women's%202017%20XL%20Hybrid/add_to_cart 2017-09-01T18:26:00Z o'brien men's neoprene life vest indoor outdoor games 9/1/2017 18:26 Sep 18 fan shop 62.206.64.9 /department/fan%20shop/category/indoor/outdoor%20games/product/O'Brien%20Men's%20Neoprene%20Life%20Vest 2017-09-01T18:26:00Z nike men's comfort 2 slide tennis & racquet 9/1/2017 18:26 Sep 18 fitness 42.220.36.253 /department/fitness/category/tennis%20&%20racquet/product/Nike%20Men's%20Comfort%202%20Slide 2017-09-01T18:26:00Z adidas kids' rg iii mid football cleat featured shops 9/1/2017 18:26 Sep 18 apparel 212.11.137.222 /department/apparel/category/featured%20shops/product/adidas%20Kids'%20RG%20III%20Mid%20Football%20Cleat 2017-09-01T18:26:00Z diamondback women's serene classic comfort bi camping & hiking 9/1/2017 18:27 Sep 18 fan shop 7.218.119.117 /department/fan%20shop/category/camping%20&%20hiking/product/Diamondback%20Women's%20Serene%20Classic%20Comfort%20Bi 2017-09-01T18:27:00Z adidas kids' rg iii mid football cleat featured shops 9/1/2017 18:27 Sep 18 apparel 88.169.187.201 /department/apparel/category/featured%20shops/product/adidas%20Kids'%20RG%20III%20Mid%20Football%20Cleat/add_to_cart 2017-09-01T18:27:00Z bridgestone e6 straight distance nfl tennesse electronics 9/1/2017 18:28 Sep 18 outdoors 25.45.74.1 /department/outdoors/category/electronics/product/Bridgestone%20e6%20Straight%20Distance%20NFL%20Tennesse 2017-09-01T18:28:00Z pelican sunstream 100 kayak water sports 9/1/2017 18:28 Sep 18 fan shop 113.89.175.180 /department/fan%20shop/category/water%20sports/product/Pelican%20Sunstream%20100%20Kayak 2017-09-01T18:28:00Z bridgestone e6 straight distance nfl san dieg electronics 9/1/2017 18:28 Sep 18 outdoors 198.195.205.47 /department/outdoors/category/electronics/product/Bridgestone%20e6%20Straight%20Distance%20NFL%20San%20Dieg 2017-09-01T18:28:00Z diamondback boys' insight 24 performance hybr basketball 9/1/2017 18:29 Sep 18 fitness 61.230.25.199 /department/fitness/category/basketball/product/Diamondback%20Boys'%20Insight%2024%20Performance%20Hybr/add_to_cart 2017-09-01T18:29:00Z adidas kids' rg iii mid football cleat featured shops 9/1/2017 18:30 Sep 18 apparel 88.169.187.201 /department/apparel/category/featured%20shops/product/adidas%20Kids'%20RG%20III%20Mid%20Football%20Cleat 2017-09-01T18:30:00Z top flite women's 2017 xl hybrid golf apparel 9/1/2017 18:30 Sep 18 outdoors 163.146.66.198 /department/outdoors/category/golf%20apparel/product/Top%20Flite%20Women's%202017%20XL%20Hybrid 2017-09-01T18:30:00Z adidas kids' rg iii mid football cleat featured shops 9/1/2017 18:30 Sep 18 apparel 21.45.244.105 /department/apparel/category/featured%20shops/product/adidas%20Kids'%20RG%20III%20Mid%20Football%20Cleat/add_to_cart 2017-09-01T18:30:00Z columbia men's pfg anchor tough t-shirt shop by sport 9/1/2017 18:30 Sep 18 golf 183.8.167.21 /department/golf/category/shop%20by%20sport/product/Columbia%20Men's%20PFG%20Anchor%20Tough%20T-Shirt 2017-09-01T18:30:00Z lija women's eyelet sleeveless golf polo golf shoes 9/1/2017 18:31 Sep 18 outdoors 142.64.203.5 /department/outdoors/category/golf%20shoes/product/LIJA%20Women's%20Eyelet%20Sleeveless%20Golf%20Polo 2017-09-01T18:31:00Z under armour girls' toddler spine surge runni shop by sport 9/1/2017 18:31 Sep 18 golf 200.42.145.101 /department/golf/category/shop%20by%20sport/produc

root
 |-- product: string (nullable = true)
 |-- category: string (nullable = true)
 |-- DATE: string (nullable = true)
 |-- MONTH: string (nullable = true)
 |-- HOUR: integer (nullable = true)
 |-- department: string (nullable = true)
 |-- ip: string (nullable = true)
 |-- url: string (nullable = true)
 |-- event_ts: timestamp (nullable = true)



In [0]:
display(df_logs.limit(10))

product category DATE MONTH HOUR department ip url event_ts perfect fitness perfect rip deck cleats 9/1/2017 18:25 Sep 18 apparel 19.239.13.199 /department/apparel/category/cleats/product/Perfect%20Fitness%20Perfect%20Rip%20Deck 2017-09-01T18:25:00Z yakima doubledown ace hitch mount 4-bike rack strength training 9/1/2017 18:25 Sep 18 footwear 61.230.25.199 /department/footwear/category/strength%20training/product/Yakima%20DoubleDown%20Ace%20Hitch%20Mount%204-Bike%20Rack 2017-09-01T18:25:00Z top flite women's 2017 xl hybrid golf apparel 9/1/2017 18:26 Sep 18 outdoors 16.231.175.0 /department/outdoors/category/golf%20apparel/product/Top%20Flite%20Women's%202017%20XL%20Hybrid/add_to_cart 2017-09-01T18:26:00Z o'brien men's neoprene life vest indoor outdoor games 9/1/2017 18:26 Sep 18 fan shop 62.206.64.9 /department/fan%20shop/category/indoor/outdoor%20games/product/O'Brien%20Men's%20Neoprene%20Life%20Vest 2017-09-01T18:26:00Z nike men's comfort 2 slide tennis & racquet 9/1/2017 18:26 Sep 18 fitness 42.220.36.253 /department/fitness/category/tennis%20&%20racquet/product/Nike%20Men's%20Comfort%202%20Slide 2017-09-01T18:26:00Z adidas kids' rg iii mid football cleat featured shops 9/1/2017 18:26 Sep 18 apparel 212.11.137.222 /department/apparel/category/featured%20shops/product/adidas%20Kids'%20RG%20III%20Mid%20Football%20Cleat 2017-09-01T18:26:00Z diamondback women's serene classic comfort bi camping & hiking 9/1/2017 18:27 Sep 18 fan shop 7.218.119.117 /department/fan%20shop/category/camping%20&%20hiking/product/Diamondback%20Women's%20Serene%20Classic%20Comfort%20Bi 2017-09-01T18:27:00Z adidas kids' rg iii mid football cleat featured shops 9/1/2017 18:27 Sep 18 apparel 88.169.187.201 /department/apparel/category/featured%20shops/product/adidas%20Kids'%20RG%20III%20Mid%20Football%20Cleat/add_to_cart 2017-09-01T18:27:00Z bridgestone e6 straight distance nfl tennesse electronics 9/1/2017 18:28 Sep 18 outdoors 25.45.74.1 /department/outdoors/category/electronics/product/Bridgestone%20e6%20Straight%20Distance%20NFL%20Tennesse 2017-09-01T18:28:00Z pelican sunstream 100 kayak water sports 9/1/2017 18:28 Sep 18 fan shop 113.89.175.180 /department/fan%20shop/category/water%20sports/product/Pelican%20Sunstream%20100%20Kayak 2017-09-01T18:28:00Z

In [0]:
from pyspark.sql import functions as F

df_logs_g = (
    df_logs
    .withColumn("product_clean", F.lower(F.col("product")))
    .withColumn("log_year", F.year("event_ts"))
    .withColumn("log_month", F.month("event_ts"))
    .withColumn("log_ym", F.date_format("event_ts", "yyyy-MM"))
    .withColumn("url_length", F.length("url"))
)


In [0]:
df_logs_g.show(5)

+--------------------+--------------------+--------------+-----+----+----------+-------------+--------------------+-------------------+--------------------+--------+---------+-------+----------+
|             product|            category|          DATE|MONTH|HOUR|department|           ip|                 url|           event_ts|       product_clean|log_year|log_month| log_ym|url_length|
+--------------------+--------------------+--------------+-----+----+----------+-------------+--------------------+-------------------+--------------------+--------+---------+-------+----------+
|perfect fitness p...|              cleats|9/1/2017 18:25|  Sep|  18|   apparel|19.239.13.199|/department/appar...|2017-09-01 18:25:00|perfect fitness p...|    2017|        9|2017-09|        84|
|yakima doubledown...|   strength training|9/1/2017 18:25|  Sep|  18|  footwear|61.230.25.199|/department/footw...|2017-09-01 18:25:00|yakima doubledown...|    2017|        9|2017-09|       115|
|top flite women's...|   

In [0]:
df_logs_monthly = (
    df_logs_g
    .withColumn("is_add_to_cart", F.col("url").contains("add_to_cart").cast("int"))
    .withColumn("is_morning", F.when((F.col("HOUR") >= 5) & (F.col("HOUR") < 12), 1).otherwise(0))
    .withColumn("is_afternoon", F.when((F.col("HOUR") >= 12) & (F.col("HOUR") < 17), 1).otherwise(0))
    .withColumn("is_evening", F.when((F.col("HOUR") >= 17) & (F.col("HOUR") < 22), 1).otherwise(0))
    .groupBy("product_clean", "log_ym")
    .agg(
        F.count("*").alias("web_views_month"),
        F.countDistinct("ip").alias("web_unique_ips_month"),
        F.sum("is_add_to_cart").alias("web_add_to_cart_month"),
        F.avg("url_length").alias("web_avg_url_length"),
        F.sum("is_morning").alias("web_morning_views"),
        F.sum("is_afternoon").alias("web_afternoon_views"),
        F.sum("is_evening").alias("web_evening_views")
    )
)


In [0]:
df_logs_monthly = df_logs_monthly.withColumn(
    "conversion_rate",
    F.col("web_add_to_cart_month") / F.col("web_views_month")
)


In [0]:
from pyspark.sql.window import Window

w = Window.partitionBy("product_clean").orderBy("log_ym")

df_logs_monthly = df_logs_monthly.withColumn(
    "views_3m",
    F.sum("web_views_month").over(w.rowsBetween(-2, 0))
)

df_logs_monthly = df_logs_monthly.withColumn(
    "views_6m",
    F.sum("web_views_month").over(w.rowsBetween(-5, 0))
)

df_logs_monthly = df_logs_monthly.withColumn(
    "momentum_score",
    F.col("views_3m") / F.col("views_6m")
)


In [0]:
df_logs_monthly.show(10)


+--------------------+-------+---------------+--------------------+---------------------+------------------+-----------------+-------------------+-----------------+-------------------+--------+--------+------------------+
|       product_clean| log_ym|web_views_month|web_unique_ips_month|web_add_to_cart_month|web_avg_url_length|web_morning_views|web_afternoon_views|web_evening_views|    conversion_rate|views_3m|views_6m|    momentum_score|
+--------------------+-------+---------------+--------------------+---------------------+------------------+-----------------+-------------------+-----------------+-------------------+--------+--------+------------------+
|adidas brazuca 20...|2017-09|           1371|                 810|                  364|113.18599562363238|              151|                318|              632|0.26549963530269877|    1371|    1371|               1.0|
|adidas brazuca 20...|2017-10|            815|                 635|                  193|112.84171779141104|    

In [0]:
df_logs_monthly.write.format("delta").mode("overwrite").save(
    "abfss://fgold@storagedatafactory2605.dfs.core.windows.net/logs_monthly_delta/"
)


In [0]:
display(dbutils.fs.ls("abfss://fgold@storagedatafactory2605.dfs.core.windows.net/logs_monthly_delta/"))


path name size modificationTime abfss://fgold@storagedatafactory2605.dfs.core.windows.net/logs_monthly_delta/_delta_log/ _delta_log/ 0 1763224164000 abfss://fgold@storagedatafactory2605.dfs.core.windows.net/logs_monthly_delta/part-00000-707bb543-4d95-46fe-92a6-9885cff73de5.c000.snappy.parquet part-00000-707bb543-4d95-46fe-92a6-9885cff73de5.c000.snappy.parquet 26045 1763224165000

In [0]:
api_silver_path = "abfss://fsilver@storagedatafactory2605.dfs.core.windows.net/api_docs_delta/"

df_api = spark.read.format("delta").load(api_silver_path)

display(df_api)
df_api.printSchema()


description field_name Days of scheduled delivery of the purchased product days_for_shipment_scheduled_ Link of visit and purchase of the product product_image Country where the customer made the purchase customer_country Customer Zipcode customer_zipcode The following shipping modes are presented : Standard Class , First Class , Second Class , Same Day shipping_mode Total amount per order order_item_total Order item code order_item_id Customer name customer_fname Order code order_id Order Profit Per Order order_profit_per_order Product code generated through the RFID reader order_item_cardprod_id Longitude corresponding to location of store longitude Customer order code order_customer_id Exact date and time of shipment shipping_date_dateorders_ Delivery status of orders: Advance shipping , Late delivery , Shipping canceled , Shipping on time delivery_status State to which the store where the purchase is registered belongs customer_state Order item discount percentage order_item_discount_rate Masked customer key customer_password Customer ID customer_id Status of the product stock :If it is 1 not available , 0 the product is available product_status Order item discount value order_item_discount Street to which the store where the purchase is registered belongs customer_street Description of the product category category_name Region of the world where the order is delivered : Southeast Asia ,South Asia ,Oceania ,Eastern Asia, West Asia , West of USA , US Center , West Africa, Central Africa ,North Africa ,Western Europe ,Northern , Caribbean , South America ,East Africa ,Southern Europe , East of USA ,Canada ,Southern Africa , Central Asia , Europe , Central America, Eastern Europe , South of USA order_region Latitude corresponding to location of store latitude State of the region where the order is delivered order_state Number of products per order order_item_quantity Customer's email customer_email Date on which the order is made order_date_dateorders_ Customer lastname customer_lname Product category code category_id Total sales per customer made per customer sales_per_customer Order Item Profit Ratio order_item_profit_ratio Categorical variable that indicates if sending is late (1), it is not late (0). late_delivery_risk Product Price product_price Product Name product_name Types of Customers: Consumer , Corporate , Home Office customer_segment Price of products without discount order_item_product_price Department code of store department_id Product code product_card_id Type of transaction made type Destination country of the order order_country Earnings per order placed benefit_per_order Product category code product_category_id Market to where the order is delivered : Africa , Europe , LATAM , Pacific Asia , USCA market Destination city of the order order_city Value in sales sales Order Status : COMPLETE , PENDING , CLOSED , PENDING_PAYMENT ,CANCELED , PROCESSING ,SUSPECTED_FRAUD ,ON_HOLD ,PAYMENT_REVIEW order_status Product Description product_description Actual shipping days of the purchased product days_for_shipping_real_ Department name of store department_name City where the customer made the purchase customer_city

root
 |-- description: string (nullable = true)
 |-- field_name: string (nullable = true)



In [0]:
######################
sales_path = "abfss://fgold@storagedatafactory2605.dfs.core.windows.net/monthly_sales_enriched_delta/"
logs_path  = "abfss://fgold@storagedatafactory2605.dfs.core.windows.net/logs_monthly_delta/"

df_sales = spark.read.format("delta").load(sales_path)
df_logs  = spark.read.format("delta").load(logs_path)

display(df_sales)
display(df_logs)


product_name category_name order_year order_month order_ym monthly_sales monthly_quantity lag_1_sales lag_3_sales rmean_3_sales target_next_month_sales mom_growth lag_12_sales yoy_growth rmean_6_sales adidas brazuca 2014 official match ball baseball & softball 2017 4 2017-04 799.9500275 5 null null 799.9500275 2399.8500825 null null null 799.9500275 adidas brazuca 2014 official match ball baseball & softball 2017 5 2017-05 2399.8500825 15 799.9500275 null 1599.900055 1919.880066 2.0 null null 1599.900055 adidas brazuca 2014 official match ball baseball & softball 2017 6 2017-06 1919.880066 12 2399.8500825 null 1706.5600586666667 2239.8600770000003 -0.20000000000000007 null null 1706.5600586666667 adidas brazuca 2014 official match ball baseball & softball 2017 7 2017-07 2239.8600770000003 14 1919.880066 799.9500275 2186.530075166667 2239.8600770000003 0.16666666666666685 null null 1839.88506325 adidas brazuca 2014 official match ball baseball & softball 2017 8 2017-08 2239.8600770000003 14 2239.8600770000003 2399.8500825 2133.2000733333334 799.9500275 0.0 null null 1919.8800660000002 adidas brazuca 2014 official match ball baseball & softball 2017 9 2017-09 799.9500275 5 2239.8600770000003 1919.880066 1759.8900605000001 null -0.6428571428571429 null null 1733.2250595833332 adidas kids' f5 messi fg soccer cleat baseball & softball 2015 1 2015-01 629.82001486 18 null null 629.82001486 699.80002208 null null null 629.82001486 adidas kids' f5 messi fg soccer cleat baseball & softball 2015 2 2015-02 699.80002208 20 629.82001486 null 664.8100184699999 454.87001414 0.11111111995314328 null null 664.8100184699999 adidas kids' f5 messi fg soccer cleat baseball & softball 2015 3 2015-03 454.87001414 13 699.80002208 null 594.8300170266666 1119.68001538 -0.35000000030294365 null null 594.8300170266666 adidas kids' f5 messi fg soccer cleat baseball & softball 2015 4 2015-04 1119.68001538 32 454.87001414 629.82001486 758.1166838666667 874.75002664 1.461538418831417 null null 726.042516615 adidas kids' f5 messi fg soccer cleat baseball & softball 2015 5 2015-05 874.75002664 25 1119.68001538 699.80002208 816.4333520533334 559.84001152 -0.21874998693879072 null null 755.7840186199999 adidas kids' f5 messi fg soccer cleat baseball & softball 2015 6 2015-06 559.84001152 16 874.75002664 454.87001414 851.4233511799999 1049.70002736 -0.3600000063213488 null null 723.1266841033333 adidas kids' f5 messi fg soccer cleat baseball & softball 2015 7 2015-07 1049.70002736 30 559.84001152 1119.68001538 828.0966885066667 699.80002586 0.8750000102886537 null null 793.1066861866666 adidas kids' f5 messi fg soccer cleat baseball & softball 2015 8 2015-08 699.80002586 20 1049.70002736 874.75002664 769.7800215799999 1224.65001656 -0.33333332607411653 null null 793.1066868166666 adidas kids' f5 messi fg soccer cleat baseball & softball 2015 9 2015-09 1224.65001656 35 699.80002586 559.84001152 991.3833565933334 279.92001344 0.7499999589954288 null null 921.4033538866665 adidas kids' f5 messi fg soccer cleat baseball & softball 2015 10 2015-10 279.92001344 8 1224.65001656 1049.70002736 734.79001862 1679.52002688 -0.7714285635448029 null null 781.4433535633334 adidas kids' f5 messi fg soccer cleat baseball & softball 2015 11 2015-11 1679.52002688 48 279.92001344 699.80002586 1061.3633522933333 1364.61001562 4.999999807945136 null null 915.5716869366667 adidas kids' f5 messi fg soccer cleat baseball & softball 2015 12 2015-12 1364.61001562 39 1679.52002688 1224.65001656 1108.0166853133333 874.75003426 -0.18750000370343897 null null 1049.7000209533333 adidas kids' f5 messi fg soccer cleat baseball & softball 2016 1 2016-01 874.75003426 25 1364.61001562 279.92001344 1306.29335892 1119.6800230200001 -0.358974341205781 629.82001486 0.38888891051587876 1020.54168877 adidas kids' f5 messi fg soccer cleat baseball & softball 2016 2 2016-02 1119.6800230200001 32 874.75003426 1679.52002688 1119.6800243 839.76000198 0.2799999761842823 699.80002208 0.5999999824121186 1090.52168

product_clean log_ym web_views_month web_unique_ips_month web_add_to_cart_month web_avg_url_length web_morning_views web_afternoon_views web_evening_views conversion_rate views_3m views_6m momentum_score adidas brazuca 2017 official match ball 2017-09 1371 810 364 113.18599562363238 151 318 632 0.26549963530269877 1371 1371 1.0 adidas brazuca 2017 official match ball 2017-10 815 635 193 112.84171779141104 103 313 304 0.23680981595092024 2186 2186 1.0 adidas brazuca 2017 official match ball 2017-11 828 626 219 113.17391304347827 127 293 282 0.2644927536231884 3014 3014 1.0 adidas brazuca 2017 official match ball 2017-12 831 644 202 112.91696750902527 108 311 314 0.2430806257521059 2474 3845 0.6434330299089727 adidas brazuca 2017 official match ball 2018-01 857 649 230 113.22053675612602 130 300 298 0.26837806301050177 2516 4702 0.5350914504466184 adidas kids' f5 messi fg soccer cleat 2017-09 1434 826 387 113.23849372384937 153 368 636 0.2698744769874477 1434 1434 1.0 adidas kids' f5 messi fg soccer cleat 2017-10 821 630 213 113.11327649208283 136 303 269 0.25943970767356883 2255 2255 1.0 adidas kids' f5 messi fg soccer cleat 2017-11 849 632 225 113.18021201413427 116 332 288 0.26501766784452296 3104 3104 1.0 adidas kids' f5 messi fg soccer cleat 2017-12 836 640 218 113.12918660287082 139 311 272 0.2607655502392344 2506 3940 0.6360406091370558 adidas kids' f5 messi fg soccer cleat 2018-01 878 653 232 113.17084282460137 118 344 301 0.2642369020501139 2563 4818 0.5319634703196348 adidas kids' rg iii mid football cleat 2017-09 5946 1911 1704 107.43895055499496 686 1436 2672 0.2865792129162462 5946 5946 1.0 adidas kids' rg iii mid football cleat 2017-10 3677 1428 1047 107.41691596410116 493 1338 1323 0.2847429970084308 9623 9623 1.0 adidas kids' rg iii mid football cleat 2017-11 3452 1702 989 107.4380069524913 472 1199 1317 0.28650057937427575 13075 13075 1.0 adidas kids' rg iii mid football cleat 2017-12 3705 1439 1055 107.417004048583 478 1364 1336 0.28475033738191635 10834 16780 0.6456495828367104 adidas kids' rg iii mid football cleat 2018-01 3597 1753 1029 107.43286071726439 481 1265 1373 0.28607172643869894 10754 20377 0.5277518771163566 adidas men's germany black crest away tee 2017-09 1823 967 526 107.46242457487658 207 462 782 0.2885353812397148 1823 1823 1.0 adidas men's germany black crest away tee 2017-10 1111 759 318 107.43474347434743 156 375 445 0.28622862286228623 2934 2934 1.0 adidas men's germany black crest away tee 2017-11 1107 797 322 107.49051490514906 164 389 387 0.2908762420957543 4041 4041 1.0 adidas men's germany black crest away tee 2017-12 1093 759 313 107.43641354071363 148 374 436 0.28636779505946935 3311 5134 0.6449162446435528 adidas men's germany black crest away tee 2018-01 1139 821 332 107.49780509218613 169 401 394 0.2914837576821773 3339 6273 0.5322812051649928 adidas youth germany black/red away match soc 2017-09 1929 1023 558 111.47122861586314 220 429 896 0.2892690513219285 1929 1929 1.0 adidas youth germany black/red away match soc 2017-10 1221 801 369 111.62653562653563 189 428 419 0.3022113022113022 3150 3150 1.0 adidas youth germany black/red away match soc 2017-11 1139 794 327 111.4451273046532 150 392 427 0.2870939420544337 4289 4289 1.0 adidas youth germany black/red away match soc 2017-12 1231 812 376 111.66531275385866 185 432 424 0.30544272948822093 3591 5520 0.6505434782608696 adidas youth germany black/red away match soc 2018-01 1188 828 345 111.48484848484848 156 409 444 0.2904040404040404 3558 6708 0.5304114490161002 bag boy beverage holder 2017-09 236 165 60 84.05084745762711 23 59 83 0.2542372881355932 236 236 1.0 bag boy beverage holder 2017-10 138 130 35 84.04347826086956 16 39 57 0.2536231884057971 374 374 1.0 bag boy beverage holder 2017-11 150 134 38 84.04 27 46 51 0.25333333333333335 524 524 1.0 bag boy beverage holder 2017-12 137 126 33 83.8905109489051 17 40 57 0.24087591240875914 425 661 0.642965204236006 bag boy beverage holder 2018-01 157 140 38 83.90445859872611 28 

In [0]:
import pyspark.sql.functions as F

df_sales_clean = df_sales.withColumn(
    "product_key",
    F.lower(F.trim(F.col("product_name")))
)

df_logs_clean = df_logs.withColumn(
    "product_key",
    F.lower(F.trim(F.col("product_clean")))
)


In [0]:
df_master = (
    df_sales_clean.alias("s")
    .join(
        df_logs_clean.alias("l"),
        [
            F.col("s.product_key") == F.col("l.product_key"),
            F.col("s.order_ym") == F.col("l.log_ym")
        ],
        "left"
    )
)


In [0]:
df_gold_final = df_master.select(
    "s.product_name",
    "s.category_name",
    "s.order_year",
    "s.order_month",
    "s.order_ym",
    "s.monthly_sales",
    "s.monthly_quantity",
    "s.lag_1_sales",
    "s.lag_3_sales",
    "s.rmean_3_sales",
    "s.target_next_month_sales",
    "s.mom_growth",
    "s.yoy_growth",
    "s.rmean_6_sales",

    # logs
    "l.web_views_month",
    "l.web_unique_ips_month",
    "l.web_add_to_cart_month",
    "l.web_avg_url_length",
    "l.web_morning_views",
    "l.web_afternoon_views",
    "l.web_evening_views",
    "l.conversion_rate",
    "l.views_3m",
    "l.views_6m",
    "l.momentum_score"
)


In [0]:
df_gold_final.write.format("delta").mode("overwrite").save(
    "abfss://fgold@storagedatafactory2605.dfs.core.windows.net/df_gold_final/"
)

In [0]:
# GOLD → PARQUET EXPORT PATHS
gold_base_path = "abfss://fgold@storagedatafactory2605.dfs.core.windows.net/"

export_paths = {
    "monthly_sales_enriched": gold_base_path + "export/monthly_sales_enriched/",
    "logs_monthly": gold_base_path + "export/logs_monthly/",
    "master_gold_final": gold_base_path + "export/master_gold_final/"
}

# LOAD GOLD TABLES
df_sales = spark.read.format("delta").load(gold_base_path + "monthly_sales_enriched_delta/")
df_logs  = spark.read.format("delta").load(gold_base_path + "logs_monthly_delta/")
df_master = spark.read.format("delta").load(gold_base_path + "df_gold_final/")

# SAVE AS PARQUET
df_sales.write.mode("overwrite").parquet(export_paths["monthly_sales_enriched"])
df_logs.write.mode("overwrite").parquet(export_paths["logs_monthly"])
df_master.write.mode("overwrite").parquet(export_paths["master_gold_final"])

print("🎉 Gold Layer Export Completed")
for name, path in export_paths.items():
    print(f"{name} → {path}")


🎉 Gold Layer Export Completed
monthly_sales_enriched → abfss://fgold@storagedatafactory2605.dfs.core.windows.net/export/monthly_sales_enriched/
logs_monthly → abfss://fgold@storagedatafactory2605.dfs.core.windows.net/export/logs_monthly/
master_gold_final → abfss://fgold@storagedatafactory2605.dfs.core.windows.net/export/master_gold_final/
